In [7]:
import nltk
from nltk.corpus import stopwords
import string
from nltk import word_tokenize, FreqDist
from sklearn.feature_extraction.text import TfidfVectorizer
import matplotlib.pyplot as plt
from datetime import datetime

import pandas as pd 
import numpy as np
from bs4 import BeautifulSoup
import requests
import json
from time import sleep, time
import lxml
import re
from urllib.parse import urljoin
import unicodedata
from collections import defaultdict, Counter
import WebScrape_Indeed
import WebScrape_LinkedIn
import streamlit as st 
import terms 
import Cities 
import functions
import time
import pandas_profiling as pp

import plotly.graph_objects as go

In [65]:
d = pd.read_csv('total_data_date.csv')


In [66]:
d.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15742 entries, 0 to 15741
Data columns (total 5 columns):
title          15420 non-null object
company        14897 non-null object
location       14897 non-null object
description    15742 non-null object
date           15742 non-null object
dtypes: object(5)
memory usage: 615.0+ KB


In [67]:
d.isna().sum()

title          322
company        845
location       845
description      0
date             0
dtype: int64

In [68]:
d.dropna(inplace=True)

In [69]:
d.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 14897 entries, 0 to 15741
Data columns (total 5 columns):
title          14897 non-null object
company        14897 non-null object
location       14897 non-null object
description    14897 non-null object
date           14897 non-null object
dtypes: object(5)
memory usage: 698.3+ KB


In [8]:
pp.ProfileReport(d)

In [70]:
d.duplicated(['description']).sum()

12178

In [14]:
ditto = d.copy()

In [62]:
ditto

title  \
0                       Data Scientist   
1                       DATA SCIENTIST   
2                       Data Scientist   
3                       DATA SCIENTIST   
5      Staff Data Scientist (GEC11903)   
...                                ...   
15737                   Data Scientist   
15738       Data Scientist / Economist   
15739       Data Scientist - Mid-Level   
15740                   Data Scientist   
15741                   Data Scientist   

                                       company                  location  \
0                                     Esurance   San Francisco, CA 94105   
1                                      Walmart       Sunnyvale, CA 94087   
2                                       Kohl's        Milpitas, CA 95035   
3                            Walmart eCommerce       Sunnyvale, CA 94087   
5                            Walmart eCommerce       Sunnyvale, CA 94087   
...                                        ...                       ...   
15737                           Seen by Indeed         San Francisco, CA   
15738                                eBay Inc.              San Jose, CA   
15739  National Geospatial-Intelligence Agency  Wright-Patterson AFB, OH   
15740                                  Verizon      Alpharetta, GA 30004   
15741                                    GEICO           Chevy Chase, MD   

                                             description        date  
0      [     Summary       Esurance is looking for a ...  12-01-2019  
1      [     Position Description    Data Scientist i...  12-01-2019  
2      [  Interpret and apply data analyses and expla...  12-01-2019  
3      [     Position Description    Data Scientist i...  12-01-2019  
5      [     Position Description      Understands an...  12-01-2019  
...                                                  ...         ...  
15737  [    With one application you can be considere...  12-18-2019  
15738  [    Looking for a company that inspires passi...  12-18-2019  
15739  [   Data Scientists develop and apply methods ...  12-18-2019  
15740  [     What you’ll be doing...    Be a part of ...  12-18-2019  
15741  [    GEICO’s Data Science team uses predictive...  12-18-2019  

[14897 rows x 5 columns]

In [72]:
d = d.drop_duplicates(subset=['description'], keep='first').reset_index(drop=True)

In [75]:
d.date.unique()

array(['12-01-2019', '12-07-2019', '12-10-2019', '12-12-2019',
       '12-14-2019', '12-15-2019', '12-16-2019', '12-17-2019',
       '12-18-2019'], dtype=object)

In [74]:
pp.ProfileReport(d)

In [44]:
d.date = pd.to_datetime(d.date, format="%m-%d-%Y")

In [78]:
ditto.to_csv('/users/dmauger/Flatiron/FinalProject/' + 'total_data_backup.csv', mode='w', encoding='utf-8', index=False)

In [79]:
f = pd.read_csv('total_data_backup.csv')
f

title  \
0                       Data Scientist   
1                       DATA SCIENTIST   
2                       Data Scientist   
3                       DATA SCIENTIST   
4      Staff Data Scientist (GEC11903)   
...                                ...   
14892                   Data Scientist   
14893       Data Scientist / Economist   
14894       Data Scientist - Mid-Level   
14895                   Data Scientist   
14896                   Data Scientist   

                                       company                  location  \
0                                     Esurance   San Francisco, CA 94105   
1                                      Walmart       Sunnyvale, CA 94087   
2                                       Kohl's        Milpitas, CA 95035   
3                            Walmart eCommerce       Sunnyvale, CA 94087   
4                            Walmart eCommerce       Sunnyvale, CA 94087   
...                                        ...                       ...   
14892                           Seen by Indeed         San Francisco, CA   
14893                                eBay Inc.              San Jose, CA   
14894  National Geospatial-Intelligence Agency  Wright-Patterson AFB, OH   
14895                                  Verizon      Alpharetta, GA 30004   
14896                                    GEICO           Chevy Chase, MD   

                                             description        date  
0      [     Summary       Esurance is looking for a ...  12-01-2019  
1      [     Position Description    Data Scientist i...  12-01-2019  
2      [  Interpret and apply data analyses and expla...  12-01-2019  
3      [     Position Description    Data Scientist i...  12-01-2019  
4      [     Position Description      Understands an...  12-01-2019  
...                                                  ...         ...  
14892  [    With one application you can be considere...  12-18-2019  
14893  [    Looking for a company that inspires passi...  12-18-2019  
14894  [   Data Scientists develop and apply methods ...  12-18-2019  
14895  [     What you’ll be doing...    Be a part of ...  12-18-2019  
14896  [    GEICO’s Data Science team uses predictive...  12-18-2019  

[14897 rows x 5 columns]

In [80]:
d.to_csv('/users/dmauger/Flatiron/FinalProject/' + 'total_data_date.csv', mode='w', encoding='utf-8', index=False)

In [81]:
d = pd.read_csv('total_data_date.csv')
d

title              company  \
0                      Data Scientist             Esurance   
1                      DATA SCIENTIST              Walmart   
2                      Data Scientist               Kohl's   
3     Staff Data Scientist (GEC11903)    Walmart eCommerce   
4                  Sr. Data Scientist  Silicon Valley Bank   
...                               ...                  ...   
2714                   Data Scientist  Lifescale Analytics   
2715                   Data Scientist              Averity   
2716                   Data Scientist        M-Logic, Inc.   
2717               SAS Data Scientist      Lawrence Harvey   
2718              Lead Data Scientist              Safeway   

                                    location  \
0                    San Francisco, CA 94105   
1                        Sunnyvale, CA 94087   
2                         Milpitas, CA 95035   
3                        Sunnyvale, CA 94087   
4                        Palo Alto, CA 94304   
...                                      ...   
2714  Raleigh, North Carolina, United States   
2715         New York City Metropolitan Area   
2716                      New York, New York   
2717      Arlington, Virginia, United States   
2718                  Pleasanton, California   

                                            description        date  
0     [     Summary       Esurance is looking for a ...  12-01-2019  
1     [     Position Description    Data Scientist i...  12-01-2019  
2     [  Interpret and apply data analyses and expla...  12-01-2019  
3     [     Position Description      Understands an...  12-01-2019  
4     [       Silicon Valley Bank is the market lead...  12-01-2019  
...                                                 ...         ...  
2714  At Lifescale Analytics, we help life science o...  12-18-2019  
2715  Are you an experienced Data Scientist who is l...  12-18-2019  
2716  *Candidate must be able to work in the US with...  12-18-2019  
2717  My client, is a world leading CPG company that...  12-18-2019  
2718  Albertsons-Safeway Company is one of the large...  12-18-2019  

[2719 rows x 5 columns]

In [82]:
pp.ProfileReport(d)

In [83]:
d.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2719 entries, 0 to 2718
Data columns (total 5 columns):
title          2719 non-null object
company        2719 non-null object
location       2719 non-null object
description    2719 non-null object
date           2719 non-null object
dtypes: object(5)
memory usage: 106.3+ KB


In [84]:
df = pd.read_csv('total_data_date.csv')
df.head()

title              company  \
0                   Data Scientist             Esurance   
1                   DATA SCIENTIST              Walmart   
2                   Data Scientist               Kohl's   
3  Staff Data Scientist (GEC11903)    Walmart eCommerce   
4               Sr. Data Scientist  Silicon Valley Bank   

                  location                                        description  \
0  San Francisco, CA 94105  [     Summary       Esurance is looking for a ...   
1      Sunnyvale, CA 94087  [     Position Description    Data Scientist i...   
2       Milpitas, CA 95035  [  Interpret and apply data analyses and expla...   
3      Sunnyvale, CA 94087  [     Position Description      Understands an...   
4      Palo Alto, CA 94304  [       Silicon Valley Bank is the market lead...   

         date  
0  12-01-2019  
1  12-01-2019  
2  12-01-2019  
3  12-01-2019  
4  12-01-2019

In [85]:
pp.ProfileReport(df)